In [1]:
import xml.etree.ElementTree as ET
# import flexible01 as flibl
import flexible05 as flibl
import re
from typing import OrderedDict

In [2]:
file_name = "./data/tca_201908_child_child6_cci_video_ahs_gaze_vc_recoded-test.eaf" # or whatever file'
eaf_parsed = ET.parse(file_name)
eaf_root = eaf_parsed.getroot()
media_guid = flibl.generate_guid()

document = ET.ElementTree(ET.Element("document"))
document_root = document.getroot()
interlinear_text = ET.Element("interlinear-text", attrib={"guid":flibl.generate_guid()})
# Remove the tiers that use the "Included In" stereotype constraint
flibl.remove_included_in(eaf_root)
title = ET.Element("item", attrib={"type":"title", "lang":"en"}) # althought the language shouldn't be en, but idk what to do here
eaf_split_pattern = re.compile("[^/]+\.eaf")
title_match = eaf_split_pattern.search(file_name)[0][:-4]
# title_spec = input("This program will use file name ({}) for title unless specified here (enter/return to continue)\n".format(title_match))
# if title_spec:
#     title.text = title_spec
# else:
#     title.text = title_match
title.text = title_match
interlinear_text.append(title)

paragraphs = ET.Element("paragraphs")

In [3]:
# Make tier groups
top_tiers = []
# Populate the top-level tiers
for i in eaf_root.findall("TIER"):
    if "PARENT_REF" not in i.attrib.keys():
        top_tiers.append({
            "PARENT_TIER_ID": i.attrib["TIER_ID"],
            "PARTICIPANT": i.attrib["PARTICIPANT"],
            "PARENT_TIER": i,
            "CHILD_TIERS": []
        })

In [4]:
# Populate the child tiers
for i in eaf_root.findall("TIER"):
    if "PARENT_REF" in i.attrib.keys():
        for j in top_tiers:
            if j["PARENT_TIER_ID"] == i.attrib["PARENT_REF"]:
                j["CHILD_TIERS"].append(i)
                break

In [5]:
# Get dict oftime IDs and their values
times = flibl.time_values(eaf_root)

In [7]:
translation_tiers = {"Child4-tns-abs":"es", "Caregiver-tns-abs":"es", "AHS-tns-abs":"es", "Child9-tns-abs":"es", "MA1-tns-abs":"es", "Child4-tns":"en", "Caregiver-tns":"en", "AHS-tns":"en", "Child9-tns":"en", "MA1-tns":"en"}

In [12]:
annotations = OrderedDict()
for alignable_tier in top_tiers:
    for annotation in alignable_tier["PARENT_TIER"]:
        annotation_id = annotation[0].attrib["ANNOTATION_ID"]
        annotation_content = {}
        annotation_content["guid"] = flibl.generate_guid()
        annotation_content["begin-time-offset"] = times[annotation[0].attrib["TIME_SLOT_REF1"]]
        annotation_content["end-time-offset"] = times[annotation[0].attrib["TIME_SLOT_REF2"]]
        annotation_content["text"] = annotation[0][0].text
        annotation_content["speaker"] = alignable_tier["PARTICIPANT"]
        annotation_content["media-file"] = media_guid
        annotation_content["CHILD_TIERS"] = {}
        annotations[annotation_id] = annotation_content
    # Get the note/translations into the CHILD_TIERS--these won't be tokenized, rather placed as full strings at the phrase level
    for reference_tier in alignable_tier["CHILD_TIERS"]:
        # translation = input("Is the tier {} a translation tier? Enter any character for yes, hit enter/return for no: ".format(reference_tier.attrib["TIER_ID"]))
        
        for annotation in reference_tier:
            this_annotation_id = annotation[0].attrib["ANNOTATION_REF"]
            # annotation[0][0].attrib["is-translation"]
            # if translation:
            #     annotation[0][0].attrib["translation"] = 1
            # else:
            #     annotation[0][0].attrib["translation"] = 0

            # going based on user defined things in the file, in translation_tiers, instead of input at runtime. If doing this, 
            # if reference_tier.attrib["TIER_ID"] in translation_tiers["en"]:
            #     annotation[0][0].attrib["translation"] = "en"
            # elif reference_tier.attrib["TIER_ID"] in translation_tiers["es"]:
            #     annotation[0][0].attrib["translation"] = "es"
            # else:
            #     annotation[0][0].attrib["translation"] = ""
            if reference_tier.attrib["TIER_ID"] in translation_tiers.keys():
                annotation[0][0].attrib["translation"] = translation_tiers[reference_tier.attrib["TIER_ID"]]
                break
            else:
                annotation[0][0].attrib["translation"] = ""
                continue
            # annotations[this_annotation_id]["CHILD_TIERS"][reference_tier.attrib["LINGUISTIC_TYPE_REF"]] = annotation[0][0]
            annotations[this_annotation_id]["CHILD_TIERS"][reference_tier.attrib["TIER_ID"]] = annotation[0][0]

In [13]:
translation_tiers[reference_tier.attrib["TIER_ID"]]

KeyError: 'MA1-xds'

In [7]:
# the translation attribute assignment is working, and it certainly isn't being picked up when i'm trying to read it (and it's because the thing i'm assigning is just the text, so it loses the actual element). it's because we're assigning the translation attribute to the tier located in top_tiers!! duh!!
reference_tier

<Element 'TIER' at 0x7f29841a9ef0>

In [8]:
flibl.print_el_info(annotation_dict["CHILD_TIERS"]["xds"])

NameError: name 'annotation_dict' is not defined

In [ ]:
# Can we re-order things in the paragraphs variable straight up? like just go by the begin-time-offset? we know we can use the append method for elements, and we can index them like lists, can we sort them too?
seg_count = 1
for annotation in annotations:
    annotation_dict = annotations[annotation]
    paragraph = ET.Element("paragraph", attrib={"guid": flibl.generate_guid()})
    phrases = ET.Element("phrases")
    phrase = ET.Element("phrase", attrib={"guid":flibl.generate_guid(), "begin-time-offset": annotation_dict["begin-time-offset"], "end-time-offset": annotation_dict["end-time-offset"], "speaker": annotation_dict["speaker"], "media-file": annotation_dict["media-file"]})
    segnum = ET.Element("item", attrib={"type":"segnum", "lang":"en"})
    segnum.text = str(seg_count)
    seg_count += 1
    phrase.append(segnum)
    text = flibl.tokenize(annotation_dict["text"], lg="tca")
    flibl.add_word_el(text, phrase)
    # Populate the text for the notes. We're putting translations here because there's otherwise no way to automatically discern which of the dependent ELAN tiers is the translation vs the notes. That is, unless we request users to use a particular naming convention. In that case, I will make sure there is a type: gls as well.
    for i in annotation_dict["CHILD_TIERS"]:
        print(i)
        print(annotation_dict)
        print(annotation_dict["CHILD_TIERS"][i])
        if annotation_dict["CHILD_TIERS"][i].attrib["translation"]:
        # if [annotation_dict["CHILD_TIERS"].find([i])]["translation"]:
            note = ET.Element("item", attrib={"type":"gls", "lang":"en"})
        else:
            note = ET.Element("item", attrib={"type":"note", "lang":"en"})
        # note = ET.Element("item", attrib={"type":"note", "lang":"en"})
        note.text = annotation_dict["CHILD_TIERS"][i].text
        phrase.append(note) # literally idk how to know what the language is going to be. and yeah, it's all notes down here for now, sorry. played with it a lot to see if i could get it to work but I can't
    phrases.append(phrase)
    paragraph.append(phrases)
    paragraphs.append(paragraph)
for para in sorted(paragraphs, key=lambda para: int(para[0][0].attrib["begin-time-offset"])):
    interlinear_text.append(para)

tns
{'guid': '00000000-0000-0000-0000-00000005a9d3', 'begin-time-offset': '907014', 'end-time-offset': '909288', 'text': 'pa317a2, nge17ta2 n+317#3 na4ngau1', 'speaker': 'CHI', 'media-file': '00000000-0000-0000-0000-00000005a9d1', 'CHILD_TIERS': {'tns': <Element 'ANNOTATION_VALUE' at 0x7fc4c9740830>, 'xds': <Element 'ANNOTATION_VALUE' at 0x7fc4c970fa10>}}
<Element 'ANNOTATION_VALUE' at 0x7fc4c9740830>
xds
{'guid': '00000000-0000-0000-0000-00000005a9d3', 'begin-time-offset': '907014', 'end-time-offset': '909288', 'text': 'pa317a2, nge17ta2 n+317#3 na4ngau1', 'speaker': 'CHI', 'media-file': '00000000-0000-0000-0000-00000005a9d1', 'CHILD_TIERS': {'tns': <Element 'ANNOTATION_VALUE' at 0x7fc4c9740830>, 'xds': <Element 'ANNOTATION_VALUE' at 0x7fc4c970fa10>}}
<Element 'ANNOTATION_VALUE' at 0x7fc4c970fa10>
tns
{'guid': '00000000-0000-0000-0000-00000005a9d4', 'begin-time-offset': '910072', 'end-time-offset': '912485', 'text': 'm31 m3 m3 m3', 'speaker': 'CHI', 'media-file': '00000000-0000-0000-0

In [ ]:
flibl.print_el_info(interlinear_text[4][0][0][3])

Tag: item 
Attrs: {'type': 'note', 'lang': 'en'} 
Text: A 
No. of Children: 0


In [ ]:
flibl.print_el_info(top_tiers[0]["CHILD_TIERS"][2])

Tag: TIER 
Attrs: {'DEFAULT_LOCALE': 'en', 'LINGUISTIC_TYPE_REF': 'xds', 'PARENT_REF': 'CHI-tca', 'PARTICIPANT': 'CHI', 'TIER_ID': 'CHI-xds', 'translation': 0} 
Text: 
         
No. of Children: 76


In [ ]:
flibl.print_el_info(paragraphs[0][0][0])

Tag: phrase 
Attrs: {'guid': '00000000-0000-0000-0000-0000000581da', 'begin-time-offset': '907014', 'end-time-offset': '909288', 'speaker': 'CHI', 'media-file': '00000000-0000-0000-0000-0000000580f8'} 
Text: None 
No. of Children: 4


In [ ]:
count = 0
for i in sorted(paragraphs, key=lambda para: int(para[0][0].attrib["begin-time-offset"])):
    print(i[0][0].attrib["begin-time-offset"])
    if count > 24:
        break
    count += 1

886972
886980
887006
891786
893100
893542
894950
907014
910072
913315
927193
932442
933789
939167
944650
947309
948523
956462
960071
966133
968172
971552
975224
978110
978359
984015


In [13]:
phrases_inter = interlinear_text.findall(".//phrase")
onsets = []
for i in phrases_inter:
    onsets.append(int(i.attrib["begin-time-onset"]))


In [15]:
onsets == sorted(onsets)

True

In [34]:
flextext = ET.parse("/home/sunny/Documents/lx/flexible/data/tca_201908_child_child4-child9_cci_video_ahs_gaze_vc_recoded-flexible_out-paras1.flextext").getroot()

In [35]:
flibl.print_el_info(flextext.findall(".//phrase")[0])

Tag: phrase 
Attrs: {'begin-time-offset': '366040', 'end-time-offset': '366722', 'guid': '00000000-0000-0000-0000-0000000618b1', 'media-file': '00000000-0000-0000-0000-00000006167b', 'speaker': 'Child4'} 
Text: 
           
No. of Children: 5


In [37]:
onsets = []
for i in flextext.findall(".//phrase"):
    # flibl.print_el_info(i)
    # print(i.attrib)
    onsets.append(int(i.attrib["begin-time-offset"]))
    # break

In [40]:
onsets == list(set(onsets))
print(len(onsets))
print(len(set(onsets)))

563
562


In [41]:
prev = 0
for i in onsets:
    if i == prev:
        print(i)
    prev = i

1088705
